In [1]:
import numpy as np
import pandas as pd
import copy

import torch
from torch.utils.data import TensorDataset, DataLoader
from sklearn.preprocessing import MinMaxScaler

from data import fetch_dataset
from util import move_sliding_window, num_params

from model import LSTMModel
from algorithm import fedavg,fedkd

pd.set_option('display.max_columns', None)
pd.set_option('display.max_columns', None)
np.set_printoptions(suppress=True, floatmode='fixed')

In [2]:
if torch.cuda.is_available():
    device = torch.device("cuda")
    print('running on gpu')
else:
    device = torch.device("cpu")

running on gpu


# Parameters

In [3]:
window_size = 90 # Define window_size period and split inputs/labels\
batch_size = 1024
label_col_index = 0

# seq_len = 90  # (timestamps)
hidden_dim = 50
n_layers = 2
lr = 0.0001
output_dim = 1

#fed train params
num_local_epochs = 1
max_rounds = 100 #nb of total rounds for training


# Data Preperation

In [20]:
dataframes = fetch_dataset("./heterog")

Floor0
Floor1
Floor10
Floor11
Floor12
Floor13
Floor14
Floor15
Floor16
Floor17
Floor18
Floor19
Floor2
Floor20
Floor21
Floor22
Floor23
Floor24
Floor25
Floor26
Floor27
Floor28
Floor29
Floor3
Floor30
Floor31
Floor32
Floor33
Floor34
Floor35
Floor36
Floor37
Floor38
Floor39
Floor4
Floor40
Floor41
Floor42
Floor43
Floor44
Floor45
Floor46
Floor47
Floor48
Floor49
Floor5
Floor50
Floor51
Floor52
Floor53
Floor54
Floor55
Floor56
Floor57
Floor58
Floor59
Floor6
Floor60
Floor61
Floor62
Floor63
Floor64
Floor65
Floor66
Floor67
Floor68
Floor69
Floor7
Floor70
Floor71
Floor72
Floor73
Floor74
Floor75
Floor76
Floor77
Floor78
Floor79
Floor8
Floor80
Floor81
Floor82
Floor83
Floor84
Floor85
Floor86
Floor87
Floor88
Floor89
Floor9


In [21]:
n_clients = len(dataframes) #total number of clients to partition data into

In [22]:
for _, df in dataframes.items():
    print(df.columns)
    print(df.shape)

Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(68183, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(58618, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(46840, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(65390, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(57176, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(51707, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(47453, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
 

# Build the training set

In [23]:
train_loader = []
test_loader = []
label_scalers = []
for _, df in dataframes.items():
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
input_dim = next(iter(train_loader[0]))[0].shape[2]  # 22

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

# LSTM model

In [24]:
lstm = LSTMModel(input_dim, hidden_dim, output_dim, n_layers)
model_type = 'LSTM'
print(lstm)
print(num_params(lstm))

LSTMModel(
  (lstm): LSTM(9, 50, num_layers=2, batch_first=True)
  (fc): Linear(in_features=50, out_features=1, bias=True)
  (tanh): Tanh()
)
32651


# Fedkd

## 10

In [9]:
%%time
lstm_K5_kd = copy.deepcopy(lstm)
outputs_kd1, targets_kd1, loss_kd1, smape_kd1, mae_kd1, rmse_kd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_K5_kd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_kd, targets_kd, loss_kd, smape_kd, mae_kd, rmse_kd = fedkd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [0 1 2 3 4 5 6 7 8 9]
round 0, starting client 1/10, id: 0
Epoch [1/1], Train Loss: 0.13279457629289268
round 0, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.12155077035228413
round 0, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.07999229508762558
round 0, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.07486091573268941
round 0, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.11558373917530224
round 0, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.13209614953076518
round 0, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.107463252274914
round 0, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.10204959710916647
round 0, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.11473652381036012
round 0, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.1152194404276088
calc smape: 99.99999981147816%
MAE: 16.93756405948021
RMSE: 28.040365828462114
Average Loss:  0.08951917312469393

starting avg 

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0821277509742188
round 1, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.0720513429492712
round 1, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.04354197656114897
round 1, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.041801585314365536
round 1, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.06953201760969513
round 1, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.0804474659364771
round 1, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.06327751869375403
round 1, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.06006979924411728
round 1, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.06709565739664768
round 1, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.06790306370627758


C:\Users\User\anaconda3\envs\fed\lib\site-packages\sklearn\manifold\_spectral_embedding.py:274: UserWarning: Graph is not fully connected, spectral embedding may not work as expected.
  warnings.warn(


1 [0 0 0 0 0 0 0 0 0 0]
{0: 0.0}
[0.11604375 0.09974331 0.10540969 0.08520242 0.09013175 0.08102506
 0.10262550 0.11475071 0.09904673 0.10602107]
calc smape: 57.74625952457328%
MAE: 12.826743602600576
RMSE: 20.94513447950528
Average Loss:  0.050003284193534635

starting avg round 2
clients:  [0 1 2 3 4 5 6 7 8 9]
round 2, starting client 1/10, id: 0


...

1 [0 0 0 0 0 0 0 0 0 0]
{0: 0.0}
[0.11604375 0.09974331 0.10540969 0.08520242 0.09013175 0.08102506
 0.10262550 0.11475071 0.09904673 0.10602107]
calc smape: 24.88892066963473%
MAE: 1.9913708067239335
RMSE: 4.526188465842622
Average Loss:  0.0025922883157949014

starting avg round 98
clients:  [0 1 2 3 4 5 6 7 8 9]
round 98, starting client 1/10, id: 0


C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019039351263584318
round 98, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.0020143446810026136
round 98, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.0022268320778190778
round 98, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.0030057354955575796
round 98, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.0019492396606393615
round 98, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.001984834851936211
round 98, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.00218002957990393
round 98, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.0024015951975553227
round 98, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.0017188176428640472
round 98, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.0020889167487136255


C:\Users\User\anaconda3\envs\fed\lib\site-packages\sklearn\manifold\_spectral_embedding.py:274: UserWarning: Graph is not fully connected, spectral embedding may not work as expected.
  warnings.warn(


1 [0 0 0 0 0 0 0 0 0 0]
{0: 0.0}
[0.11604375 0.09974331 0.10540969 0.08520242 0.09013175 0.08102506
 0.10262550 0.11475071 0.09904673 0.10602107]
calc smape: 24.84951063103413%
MAE: 1.9904072428298314
RMSE: 4.512073287037492
Average Loss:  0.002576053439501545
CPU times: total: 22min 45s
Wall time: 22min 50s


In [10]:
loss_kd = np.insert(loss_kd, 0, loss_kd1)
smape_kd = np.insert(smape_kd, 0, smape_kd1)
mae_kd = np.insert(mae_kd, 0, mae_kd1)
rmse_kd = np.insert(mae_kd, 0, mae_kd1)

In [11]:
np.save(f'metrics/fedkd_outputs_C{n_clients}.npy', np.array(outputs_kd, dtype=object))
np.save(f'metrics/fedkd_targets_C{n_clients}.npy', np.array(targets_kd, dtype=object))
np.save(f'metrics/fedkd_loss_C{n_clients}.npy', loss_kd)
np.save(f'metrics/fedkd_smape_C{n_clients}.npy', smape_kd)
np.save(f'metrics/fedkd_mae_C{n_clients}.npy', mae_kd)
np.save(f'metrics/fedkd_rmse_C{n_clients}.npy', rmse_kd)

## 20

In [9]:
%%time
lstm_K5_kd = copy.deepcopy(lstm)
outputs_kd1, targets_kd1, loss_kd1, smape_kd1, mae_kd1, rmse_kd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_K5_kd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_kd, targets_kd, loss_kd, smape_kd, mae_kd, rmse_kd = fedkd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19]
round 0, starting client 1/20, id: 0
Epoch [1/1], Train Loss: 0.05475749300335937
round 0, starting client 2/20, id: 1
Epoch [1/1], Train Loss: 0.04580970714903541
round 0, starting client 3/20, id: 2
Epoch [1/1], Train Loss: 0.041389345967521265
round 0, starting client 4/20, id: 3
Epoch [1/1], Train Loss: 0.04608956965453486
round 0, starting client 5/20, id: 4
Epoch [1/1], Train Loss: 0.04911241824315353
round 0, starting client 6/20, id: 5
Epoch [1/1], Train Loss: 0.04508910020813347
round 0, starting client 7/20, id: 6
Epoch [1/1], Train Loss: 0.05252715466997108
round 0, starting client 8/20, id: 7
Epoch [1/1], Train Loss: 0.04284064362774479
round 0, starting client 9/20, id: 8
Epoch [1/1], Train Loss: 0.04859042690637019
round 0, starting client 10/20, id: 9
Epoch [1/1], Train Loss: 0.039831439516058664
round 0, starting client 11/20, id: 10
Epoch [1/1], Train Loss: 0.05511101800948381

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04796131774080249
round 1, starting client 2/20, id: 1
Epoch [1/1], Train Loss: 0.04034944983820122
round 1, starting client 3/20, id: 2
Epoch [1/1], Train Loss: 0.03794342087995675
round 1, starting client 4/20, id: 3
Epoch [1/1], Train Loss: 0.04126497339822498
round 1, starting client 5/20, id: 4
Epoch [1/1], Train Loss: 0.04315630680966107
round 1, starting client 6/20, id: 5
Epoch [1/1], Train Loss: 0.0400809880811721
round 1, starting client 7/20, id: 6
Epoch [1/1], Train Loss: 0.04620947739159738
round 1, starting client 8/20, id: 7
Epoch [1/1], Train Loss: 0.0375890944082782
round 1, starting client 9/20, id: 8
Epoch [1/1], Train Loss: 0.043022178220920845
round 1, starting client 10/20, id: 9
Epoch [1/1], Train Loss: 0.034681114402634126
round 1, starting client 11/20, id: 10
Epoch [1/1], Train Loss: 0.04878877735851953
round 1, starting client 12/20, id: 11
Epoch [1/1], Train Loss: 0.03133383270745215
round 1, starting client 13/20, id: 12
Epoch [1/

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.03821266189498721
round 2, starting client 2/20, id: 1
Epoch [1/1], Train Loss: 0.032189450516468945
round 2, starting client 3/20, id: 2
Epoch [1/1], Train Loss: 0.032257196959108114
round 2, starting client 4/20, id: 3
Epoch [1/1], Train Loss: 0.033559576699546734
round 2, starting client 5/20, id: 4
Epoch [1/1], Train Loss: 0.0344345652159642
round 2, starting client 6/20, id: 5
Epoch [1/1], Train Loss: 0.03243590937927365
round 2, starting client 7/20, id: 6
Epoch [1/1], Train Loss: 0.037048502649004396
round 2, starting client 8/20, id: 7
Epoch [1/1], Train Loss: 0.02975686207273096
round 2, starting client 9/20, id: 8
Epoch [1/1], Train Loss: 0.03472582594706462
round 2, starting client 10/20, id: 9
Epoch [1/1], Train Loss: 0.02695291585944316
round 2, starting client 11/20, id: 10
Epoch [1/1], Train Loss: 0.0394053083922093
round 2, starting client 12/20, id: 11
Epoch [1/1], Train Loss: 0.025262091259815187
round 2, starting client 13/20, id: 12
Epoch 

...

1 [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
calc smape: 22.829263818568684%
MAE: 1.8114863782998325
RMSE: 4.1452394287256835
Average Loss:  0.0024117097256184617

starting round 98
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19]
round 98, starting client 1/20, id: 0


C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0018016305886086005
round 98, starting client 2/20, id: 1
Epoch [1/1], Train Loss: 0.001924958902721603
round 98, starting client 3/20, id: 2
Epoch [1/1], Train Loss: 0.0020408317270468814
round 98, starting client 4/20, id: 3
Epoch [1/1], Train Loss: 0.0022337736970489373
round 98, starting client 5/20, id: 4
Epoch [1/1], Train Loss: 0.0020486498304473403
round 98, starting client 6/20, id: 5
Epoch [1/1], Train Loss: 0.001976328207820188
round 98, starting client 7/20, id: 6
Epoch [1/1], Train Loss: 0.0019323976216460198
round 98, starting client 8/20, id: 7
Epoch [1/1], Train Loss: 0.001483696628195005
round 98, starting client 9/20, id: 8
Epoch [1/1], Train Loss: 0.0024858722306537228
round 98, starting client 10/20, id: 9
Epoch [1/1], Train Loss: 0.0018912308997069316
round 98, starting client 11/20, id: 10
Epoch [1/1], Train Loss: 0.002153497530040719
round 98, starting client 12/20, id: 11
Epoch [1/1], Train Loss: 0.0019820149035168514
round 98, startin

C:\Users\User\anaconda3\envs\fed\lib\site-packages\sklearn\manifold\_spectral_embedding.py:274: UserWarning: Graph is not fully connected, spectral embedding may not work as expected.
  warnings.warn(


1 [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
calc smape: 22.730498073952294%
MAE: 1.8119945156299888
RMSE: 4.135997648991503
Average Loss:  0.002402220153784442
CPU times: total: 43min 20s
Wall time: 43min 25s


In [10]:
loss_kd = np.insert(loss_kd, 0, loss_kd1)
smape_kd = np.insert(smape_kd, 0, smape_kd1)
mae_kd = np.insert(mae_kd, 0, mae_kd1)
rmse_kd = np.insert(mae_kd, 0, mae_kd1)

In [11]:
np.save(f'metrics/fedkd_outputs_C{n_clients}.npy', np.array(outputs_kd, dtype=object))
np.save(f'metrics/fedkd_targets_C{n_clients}.npy', np.array(targets_kd, dtype=object))
np.save(f'metrics/fedkd_loss_C{n_clients}.npy', loss_kd)
np.save(f'metrics/fedkd_smape_C{n_clients}.npy', smape_kd)
np.save(f'metrics/fedkd_mae_C{n_clients}.npy', mae_kd)
np.save(f'metrics/fedkd_rmse_C{n_clients}.npy', rmse_kd)

## 30 

In [9]:
%%time
lstm_K5_kd = copy.deepcopy(lstm)
outputs_kd1, targets_kd1, loss_kd1, smape_kd1, mae_kd1, rmse_kd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_K5_kd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_kd, targets_kd, loss_kd, smape_kd, mae_kd, rmse_kd = fedkd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29]
round 0, starting client 1/30, id: 0
Epoch [1/1], Train Loss: 0.09711023553643584
round 0, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.08610431560211712
round 0, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.07380646746605636
round 0, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.07489910703517645
round 0, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.09143247540024194
round 0, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.08111857729963957
round 0, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.09926464549593023
round 0, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.08188618382193011
round 0, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.08258031065074296
round 0, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.07217192124247689
round 0, starting client 11/30, id: 10
Epoch [1/1], Tr

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.06188892991334763
round 1, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.05210267388158374
round 1, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.044623051860576704
round 1, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.049295199742796364
round 1, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.05594345000149174
round 1, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.050465409550815826
round 1, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.06143832720212035
round 1, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.047949931672159225
round 1, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.05415624978307347
round 1, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.044288128510945386
round 1, starting client 11/30, id: 10
Epoch [1/1], Train Loss: 0.06204626010730864
round 1, starting client 12/30, id: 11
Epoch [1/1], Train Loss: 0.03941981548345402
round 1, starting client 13/30, id: 12
Epoc

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04677724381381611
round 2, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.04002081975340843
round 2, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.036304905027565025
round 2, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.04065808485828195
round 2, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.04254667973145842
round 2, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.03994847759604454
round 2, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.045955921246393305
round 2, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.03583730293332407
round 2, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.043491481445156625
round 2, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.03366256867431932
round 2, starting client 11/30, id: 10
Epoch [1/1], Train Loss: 0.04771769919898362
round 2, starting client 12/30, id: 11
Epoch [1/1], Train Loss: 0.03141563973928752
round 2, starting client 13/30, id: 12
Epoch 

...

1 [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
calc smape: 21.579400136278124%
MAE: 2.0515383973482493
RMSE: 4.357270930745355
Average Loss:  0.0031997713815534123

starting round 98
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29]
round 98, starting client 1/30, id: 0


C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0016272630101017086
round 98, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.0017052288904475666
round 98, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.0019275589325439392
round 98, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.002099209570088515
round 98, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.001820913426027718
round 98, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.0017734910092258363
round 98, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.0017070930932547798
round 98, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.001348344466367842
round 98, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.0023064191325549758
round 98, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.0017072327528795635
round 98, starting client 11/30, id: 10
Epoch [1/1], Train Loss: 0.0019358790850674266
round 98, starting client 12/30, id: 11
Epoch [1/1], Train Loss: 0.0017990181819952434
round 98, starti

C:\Users\User\anaconda3\envs\fed\lib\site-packages\sklearn\manifold\_spectral_embedding.py:274: UserWarning: Graph is not fully connected, spectral embedding may not work as expected.
  warnings.warn(


1 [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
calc smape: 21.56197594239822%
MAE: 2.051453011287449
RMSE: 4.352269461506503
Average Loss:  0.0031936052790135895
CPU times: total: 1h 10min 37s
Wall time: 1h 13min 42s


In [10]:
loss_kd = np.insert(loss_kd, 0, loss_kd1)
smape_kd = np.insert(smape_kd, 0, smape_kd1)
mae_kd = np.insert(mae_kd, 0, mae_kd1)
rmse_kd = np.insert(mae_kd, 0, mae_kd1)

In [11]:
np.save(f'metrics/fedkd_outputs_C{n_clients}.npy', np.array(outputs_kd, dtype=object))
np.save(f'metrics/fedkd_targets_C{n_clients}.npy', np.array(targets_kd, dtype=object))
np.save(f'metrics/fedkd_loss_C{n_clients}.npy', loss_kd)
np.save(f'metrics/fedkd_smape_C{n_clients}.npy', smape_kd)
np.save(f'metrics/fedkd_mae_C{n_clients}.npy', mae_kd)
np.save(f'metrics/fedkd_rmse_C{n_clients}.npy', rmse_kd)

## 40

In [9]:
%%time
lstm_K5_kd = copy.deepcopy(lstm)
outputs_kd1, targets_kd1, loss_kd1, smape_kd1, mae_kd1, rmse_kd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_K5_kd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_kd, targets_kd, loss_kd, smape_kd, mae_kd, rmse_kd = fedkd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39]
round 0, starting client 1/40, id: 0
Epoch [1/1], Train Loss: 0.12076772960289471
round 0, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.10916380369000964
round 0, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.0942686896564232
round 0, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.09506895407742141
round 0, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.11492648703808134
round 0, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.10257974145933985
round 0, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.12347331441737511
round 0, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.10606631678792666
round 0, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.10338582048335901
round 0, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.09377880223716299
round 0, starting client 

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.07560398067646433
round 1, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.06529814650615057
round 1, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.05579830644031366
round 1, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.05818475348254043
round 1, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.07006153548983012
round 1, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.062332932278513914
round 1, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.07712901464185198
round 1, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.06147831467525015
round 1, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.06413198441553575
round 1, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.054541559674328687
round 1, starting client 11/40, id: 10
Epoch [1/1], Train Loss: 0.07596266797433295
round 1, starting client 12/40, id: 11
Epoch [1/1], Train Loss: 0.04971087824455216
round 1, starting client 13/40, id: 12
Epoch [

C:\Users\User\anaconda3\envs\fed\lib\site-packages\sklearn\manifold\_spectral_embedding.py:274: UserWarning: Graph is not fully connected, spectral embedding may not work as expected.
  warnings.warn(


1 [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0]
calc smape: 56.04631087339509%
MAE: 12.91611489820656
RMSE: 20.472847858121657
Average Loss:  0.05103641764272941

starting round 2
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39]
round 2, starting client 1/40, id: 0


...

1 [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0]
calc smape: 20.988061711964516%
MAE: 1.8289828604414131
RMSE: 4.226410790223443
Average Loss:  0.002670098687994126

starting round 98
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39]
round 98, starting client 1/40, id: 0


C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0016141402055201873
round 98, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.0017433783919033078
round 98, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.0018955819961977087
round 98, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.002029971136853062
round 98, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.0018626026761591106
round 98, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.001818671319051646
round 98, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.0017250999179039455
round 98, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.0013245557591907752
round 98, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.002326031231160205
round 98, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.0017340185971719347
round 98, starting client 11/40, id: 10
Epoch [1/1], Train Loss: 0.0019694339353009127
round 98, starting client 12/40, id: 11
Epoch [1/1], Train Loss: 0.0018753250754487355
round 98, starti

C:\Users\User\anaconda3\envs\fed\lib\site-packages\sklearn\manifold\_spectral_embedding.py:274: UserWarning: Graph is not fully connected, spectral embedding may not work as expected.
  warnings.warn(


1 [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0]
calc smape: 20.89338487441287%
MAE: 1.8248474471560485
RMSE: 4.212587491243708
Average Loss:  0.0026549282672657165
CPU times: total: 2h 37min 33s
Wall time: 3h 42min 15s


In [10]:
loss_kd = np.insert(loss_kd, 0, loss_kd1)
smape_kd = np.insert(smape_kd, 0, smape_kd1)
mae_kd = np.insert(mae_kd, 0, mae_kd1)
rmse_kd = np.insert(mae_kd, 0, mae_kd1)

In [11]:
np.save(f'metrics/fedkd_outputs_C{n_clients}.npy', np.array(outputs_kd, dtype=object))
np.save(f'metrics/fedkd_targets_C{n_clients}.npy', np.array(targets_kd, dtype=object))
np.save(f'metrics/fedkd_loss_C{n_clients}.npy', loss_kd)
np.save(f'metrics/fedkd_smape_C{n_clients}.npy', smape_kd)
np.save(f'metrics/fedkd_mae_C{n_clients}.npy', mae_kd)
np.save(f'metrics/fedkd_rmse_C{n_clients}.npy', rmse_kd)

## 50

In [9]:
%%time
lstm_K5_kd = copy.deepcopy(lstm)
outputs_kd1, targets_kd1, loss_kd1, smape_kd1, mae_kd1, rmse_kd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_K5_kd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_kd, targets_kd, loss_kd, smape_kd, mae_kd, rmse_kd = fedkd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49]
round 0, starting client 1/50, id: 0
Epoch [1/1], Train Loss: 0.059427552487490314
round 0, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.04938155176738898
round 0, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.04259437045806811
round 0, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.048489363809280525
round 0, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.05316385156898337
round 0, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.04829674838110806
round 0, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.0572195626996659
round 0, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.04610805220480235
round 0, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.052174848325263985
round 0, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.042573985

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0506250733544804
round 1, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.04255411475896836
round 1, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.038832903270506196
round 1, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.043513128826139016
round 1, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.04559520454230633
round 1, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.04244158300571143
round 1, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.04898625038362838
round 1, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.039115703576859444
round 1, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.04578586811056504
round 1, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.03666711184713575
round 1, starting client 11/50, id: 10
Epoch [1/1], Train Loss: 0.05088862939737736
round 1, starting client 12/50, id: 11
Epoch [1/1], Train Loss: 0.03310208243170851
round 1, starting client 13/50, id: 12
Epoch [

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04090472683310509
round 2, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.034656940607561
round 2, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.03372700732304818
round 2, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.03649791341055841
round 2, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.03706786857748574
round 2, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.03529130541719497
round 2, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.040003353327110004
round 2, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.031341075826928314
round 2, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.03783103938286121
round 2, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.0293225836077774
round 2, starting client 11/50, id: 10
Epoch [1/1], Train Loss: 0.041626239971568196
round 2, starting client 12/50, id: 11
Epoch [1/1], Train Loss: 0.02750020658009146
round 2, starting client 13/50, id: 12
Epoch [1/

...

Epoch [1/1], Train Loss: 0.0019966778180667394
round 96, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.002116130688227713
round 96, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.002380811675619851
round 96, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.0025282406622507397
round 96, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.002267271273674189
round 96, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.002220779471099377
round 96, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.002134054603457854
round 96, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.0015774745393087556
round 96, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.002830466793966481
round 96, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.0020794050535726085
round 96, starting client 11/50, id: 10
Epoch [1/1], Train Loss: 0.002409852221414136
round 96, starting client 12/50, id: 11
Epoch [1/1], Train Loss: 0.0021926297172046214
round 96, starting c

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.001992714153119486
round 97, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.002112723170365725
round 97, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.0023784060904290527
round 97, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.0025237092506323086
round 97, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.0022632375595011667
round 97, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.002216596521611791
round 97, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.002139138803515281
round 97, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.0015754220108853052
round 97, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.0028259717498888047
round 97, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.0020761563554751094
round 97, starting client 11/50, id: 10
Epoch [1/1], Train Loss: 0.00240538855723571
round 97, starting client 12/50, id: 11
Epoch [1/1], Train Loss: 0.0021894769834991737
round 97, starting 

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019887427212934026
round 98, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.002109662057935364
round 98, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.002373897231235686
round 98, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.002519429039310517
round 98, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.002258977839532731
round 98, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.002212338359095156
round 98, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.0021122963155141552
round 98, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.0015735093675518657
round 98, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.0028208961661081184
round 98, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.002072321118181139
round 98, starting client 11/50, id: 10
Epoch [1/1], Train Loss: 0.002400483965175226
round 98, starting client 12/50, id: 11
Epoch [1/1], Train Loss: 0.0021861093823405866
round 98, starting c

In [10]:
loss_kd = np.insert(loss_kd, 0, loss_kd1)
smape_kd = np.insert(smape_kd, 0, smape_kd1)
mae_kd = np.insert(mae_kd, 0, mae_kd1)
rmse_kd = np.insert(mae_kd, 0, mae_kd1)

In [11]:
np.save(f'metrics/fedkd_outputs_C{n_clients}.npy', np.array(outputs_kd, dtype=object))
np.save(f'metrics/fedkd_targets_C{n_clients}.npy', np.array(targets_kd, dtype=object))
np.save(f'metrics/fedkd_loss_C{n_clients}.npy', loss_kd)
np.save(f'metrics/fedkd_smape_C{n_clients}.npy', smape_kd)
np.save(f'metrics/fedkd_mae_C{n_clients}.npy', mae_kd)
np.save(f'metrics/fedkd_rmse_C{n_clients}.npy', rmse_kd)

## 60

In [17]:
%%time
lstm_K5_kd = copy.deepcopy(lstm)
outputs_kd1, targets_kd1, loss_kd1, smape_kd1, mae_kd1, rmse_kd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_K5_kd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_kd, targets_kd, loss_kd, smape_kd, mae_kd, rmse_kd = fedkd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59]
round 0, starting client 1/60, id: 0
Epoch [1/1], Train Loss: 0.08427680832035132
round 0, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.07339012941552536
round 0, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.06255539930942987
round 0, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.06474437144603214
round 0, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.0783473002639684
round 0, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.0694328318350017
round 0, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.08603289391140682
round 0, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.0700926515010168
round 0, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.07137548063810052
round 0, starting client 10/60, id: 9
Epoch [1/1]

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.053792720063115064
round 1, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.0443255981637372
round 1, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.038489121167610094
round 1, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.04314906917074146
round 1, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.047804631843146955
round 1, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.04314191190060228
round 1, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.05232826685784635
round 1, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.04154137124852189
round 1, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.04683251714763734
round 1, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.03784242241332928
round 1, starting client 11/60, id: 10
Epoch [1/1], Train Loss: 0.05355320030745739
round 1, starting client 12/60, id: 11
Epoch [1/1], Train Loss: 0.03355321327322407
round 1, starting client 13/60, id: 12
Epoch [

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.039954771516176886
round 2, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.03398504151652257
round 2, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.03276556626790099
round 2, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.03521588714975936
round 2, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.035972412887283346
round 2, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.03420223137363792
round 2, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.038978974360066504
round 2, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.03084615277091287
round 2, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.036727238768854975
round 2, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.028283258348151485
round 2, starting client 11/60, id: 10
Epoch [1/1], Train Loss: 0.040794553429198764
round 2, starting client 12/60, id: 11
Epoch [1/1], Train Loss: 0.026544050975261545
round 2, starting client 13/60, id: 12
Ep

...

Epoch [1/1], Train Loss: 0.00198758471392552
round 96, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.002076598446971427
round 96, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.0023333759697076557
round 96, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.0024987158899688546
round 96, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.0022354223646371715
round 96, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.0021976448057102974
round 96, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.0020917700147382104
round 96, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.00154478526465542
round 96, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.002793541187062287
round 96, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.002046281925652659
round 96, starting client 11/60, id: 10
Epoch [1/1], Train Loss: 0.002370590245845961
round 96, starting client 12/60, id: 11
Epoch [1/1], Train Loss: 0.002130238363813412
round 96, starting cli

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019830184470299847
round 97, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.0020725288441301214
round 97, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.002327924403491326
round 97, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.002492263924567869
round 97, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.002230647361350499
round 97, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.0021922709827776996
round 97, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.002090839356045566
round 97, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.0015418097851270776
round 97, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.0027875298009558507
round 97, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.002041757967230363
round 97, starting client 11/60, id: 10
Epoch [1/1], Train Loss: 0.002364849289733684
round 97, starting client 12/60, id: 11
Epoch [1/1], Train Loss: 0.002126520827388097
round 97, starting c

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.001978662128028688
round 98, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.002067963575892564
round 98, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.0023228099841314056
round 98, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.0024863657776686343
round 98, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.0022253109689865432
round 98, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.002187161632173229
round 98, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.0020900027813842968
round 98, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.0015388640288465645
round 98, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.002781418185734835
round 98, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.0020373469850272635
round 98, starting client 11/60, id: 10
Epoch [1/1], Train Loss: 0.0023588920509306863
round 98, starting client 12/60, id: 11
Epoch [1/1], Train Loss: 0.0021215653120491063
round 98, startin

In [18]:
loss_kd = np.insert(loss_kd, 0, loss_kd1)
smape_kd = np.insert(smape_kd, 0, smape_kd1)
mae_kd = np.insert(mae_kd, 0, mae_kd1)
rmse_kd = np.insert(mae_kd, 0, mae_kd1)

In [19]:
np.save(f'metrics/fedkd_outputs_C{n_clients}.npy', np.array(outputs_kd, dtype=object))
np.save(f'metrics/fedkd_targets_C{n_clients}.npy', np.array(targets_kd, dtype=object))
np.save(f'metrics/fedkd_loss_C{n_clients}.npy', loss_kd)
np.save(f'metrics/fedkd_smape_C{n_clients}.npy', smape_kd)
np.save(f'metrics/fedkd_mae_C{n_clients}.npy', mae_kd)
np.save(f'metrics/fedkd_rmse_C{n_clients}.npy', rmse_kd)

## 70

In [9]:
%%time
lstm_K5_kd = copy.deepcopy(lstm)
outputs_kd1, targets_kd1, loss_kd1, smape_kd1, mae_kd1, rmse_kd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_K5_kd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_kd, targets_kd, loss_kd, smape_kd, mae_kd, rmse_kd = fedkd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69]
round 0, starting client 1/70, id: 0
Epoch [1/1], Train Loss: 0.08507812037220541
round 0, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.07394155354963408
round 0, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.06251736676009995
round 0, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.06519884382392845
round 0, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.07903606097467919
round 0, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.06945165232755243
round 0, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.08573360590113176
round 0, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.0706756708194625
round 0, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.07224402007145377
round 0, starting

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.06104714560480614
round 1, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.05087856985628607
round 1, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.0433164635905996
round 1, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.04833436209489318
round 1, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.05485771685330705
round 1, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.04895551747176797
round 1, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.05967560672276729
round 1, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.04779486400338838
round 1, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.05277848397739805
round 1, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.04347328745104648
round 1, starting client 11/70, id: 10
Epoch [1/1], Train Loss: 0.060971298875908075
round 1, starting client 12/70, id: 11
Epoch [1/1], Train Loss: 0.03815485164523124
round 1, starting client 13/70, id: 12
Epoch [1/

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04844424374542146
round 2, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.04048370507856211
round 2, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.036667458402613796
round 2, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.041201008538551194
round 2, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.043342580299147164
round 2, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.04025160325691104
round 2, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.046330172417534364
round 2, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.03750178829397795
round 2, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.04370614571067004
round 2, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.034957874600810034
round 2, starting client 11/70, id: 10
Epoch [1/1], Train Loss: 0.0485469331421579
round 2, starting client 12/70, id: 11
Epoch [1/1], Train Loss: 0.0314319225420293
round 2, starting client 13/70, id: 12
Epoch 

...

Epoch [1/1], Train Loss: 0.0016420596220996229
round 96, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.001753112692515262
round 96, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.0019678796007711855
round 96, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.0020991584808821334
round 96, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.001858860918384215
round 96, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.0018255310693348291
round 96, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.001747614497985892
round 96, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.0013495044901369595
round 96, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.002275574394913677
round 96, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.0017347162035919067
round 96, starting client 11/70, id: 10
Epoch [1/1], Train Loss: 0.001965806351411932
round 96, starting client 12/70, id: 11
Epoch [1/1], Train Loss: 0.0018242697834993074
round 96, starting

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0016345413553282477
round 97, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.001744093631471818
round 97, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.001957553991815075
round 97, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.002087202428739664
round 97, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.001848999223015694
round 97, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.0018160572792112364
round 97, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.00173736156776195
round 97, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.0013429499077522813
round 97, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.002265341860877995
round 97, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.0017261371610436107
round 97, starting client 11/70, id: 10
Epoch [1/1], Train Loss: 0.001955036219442264
round 97, starting client 12/70, id: 11
Epoch [1/1], Train Loss: 0.001815915986969087
round 97, starting cli

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.001627454694518644
round 98, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.0017345106856535293
round 98, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.0019481743131311503
round 98, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.002075029674611583
round 98, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.0018387853832047604
round 98, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.0018063390438328496
round 98, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.0017278968809625584
round 98, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.001336391159675945
round 98, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.0022552536684088405
round 98, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.001717227552338348
round 98, starting client 11/70, id: 10
Epoch [1/1], Train Loss: 0.0019444107577631558
round 98, starting client 12/70, id: 11
Epoch [1/1], Train Loss: 0.001807488854913237
round 98, starting

In [10]:
loss_kd = np.insert(loss_kd, 0, loss_kd1)
smape_kd = np.insert(smape_kd, 0, smape_kd1)
mae_kd = np.insert(mae_kd, 0, mae_kd1)
rmse_kd = np.insert(mae_kd, 0, mae_kd1)

In [11]:
np.save(f'metrics/fedkd_outputs_C{n_clients}.npy', np.array(outputs_kd, dtype=object))
np.save(f'metrics/fedkd_targets_C{n_clients}.npy', np.array(targets_kd, dtype=object))
np.save(f'metrics/fedkd_loss_C{n_clients}.npy', loss_kd)
np.save(f'metrics/fedkd_smape_C{n_clients}.npy', smape_kd)
np.save(f'metrics/fedkd_mae_C{n_clients}.npy', mae_kd)
np.save(f'metrics/fedkd_rmse_C{n_clients}.npy', rmse_kd)

## 80

In [17]:
%%time
lstm_K5_kd = copy.deepcopy(lstm)
outputs_kd1, targets_kd1, loss_kd1, smape_kd1, mae_kd1, rmse_kd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_K5_kd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_kd, targets_kd, loss_kd, smape_kd, mae_kd, rmse_kd = fedkd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79]
round 0, starting client 1/80, id: 0
Epoch [1/1], Train Loss: 0.06449773524589135
round 0, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.05385606371694141
round 0, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.04579059945212471
round 0, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.05131055031190899
round 0, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.05792716534977611
round 0, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.051817176258191475
round 0, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.0626863690244185
round 0, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.050697486039321366
round 0, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.05

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.05343668405318036
round 1, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.0450478956517246
round 1, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.04055912554677989
round 1, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.04581675043000894
round 1, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.04807306749915533
round 1, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.044633202254772186
round 1, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.051670411803029705
round 1, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.04137933496737255
round 1, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.04825751956265706
round 1, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.03883826953393441
round 1, starting client 11/80, id: 10
Epoch [1/1], Train Loss: 0.053668731901173786
round 1, starting client 12/80, id: 11
Epoch [1/1], Train Loss: 0.03480412967895208
round 1, starting client 13/80, id: 12
Epoch [

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.045753795618437385
round 2, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.03931863899860118
round 2, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.03727832524519827
round 2, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.04122444446764738
round 2, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.04165514097125693
round 2, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.03959672120399772
round 2, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.044944635214837825
round 2, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.035255082127339424
round 2, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.042531560175120824
round 2, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.03345701957328452
round 2, starting client 11/80, id: 10
Epoch [1/1], Train Loss: 0.04674006067216395
round 2, starting client 12/80, id: 11
Epoch [1/1], Train Loss: 0.031192081833356297
round 2, starting client 13/80, id: 12
Epoc

...

Epoch [1/1], Train Loss: 0.002088365534360011
round 96, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.0022076063627739333
round 96, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.002405921939902732
round 96, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.0026396695665978627
round 96, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.0023828496235761454
round 96, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.0023482392731239083
round 96, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.002205640253787105
round 96, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.001623508619267564
round 96, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.002983100567899573
round 96, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.002180752299156868
round 96, starting client 11/80, id: 10
Epoch [1/1], Train Loss: 0.002533812650653999
round 96, starting client 12/80, id: 11
Epoch [1/1], Train Loss: 0.0022373039973899718
round 96, starting c

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.002086494791207238
round 97, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.00220480594628801
round 97, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.002403008080566198
round 97, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.0026366187581408984
round 97, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.0023796190904580403
round 97, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.002344936062581838
round 97, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.002203005241746133
round 97, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.0016224019450161887
round 97, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.002978376303172598
round 97, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.002178048983397376
round 97, starting client 11/80, id: 10
Epoch [1/1], Train Loss: 0.002529690699399604
round 97, starting client 12/80, id: 11
Epoch [1/1], Train Loss: 0.0022344660599054275
round 97, starting cli

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.002085000076682641
round 98, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.0022019769867054296
round 98, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.0024001723326768517
round 98, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.00263321862953222
round 98, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.002376185009118424
round 98, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.002341724005236756
round 98, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.002200327222109647
round 98, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.0016211487379206235
round 98, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.002973818196691215
round 98, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.002175558963682743
round 98, starting client 11/80, id: 10
Epoch [1/1], Train Loss: 0.002526182432726879
round 98, starting client 12/80, id: 11
Epoch [1/1], Train Loss: 0.0022317712627179724
round 98, starting cli

In [18]:
loss_kd = np.insert(loss_kd, 0, loss_kd1)
smape_kd = np.insert(smape_kd, 0, smape_kd1)
mae_kd = np.insert(mae_kd, 0, mae_kd1)
rmse_kd = np.insert(mae_kd, 0, mae_kd1)

In [19]:
np.save(f'metrics/fedkd_outputs_C{n_clients}.npy', np.array(outputs_kd, dtype=object))
np.save(f'metrics/fedkd_targets_C{n_clients}.npy', np.array(targets_kd, dtype=object))
np.save(f'metrics/fedkd_loss_C{n_clients}.npy', loss_kd)
np.save(f'metrics/fedkd_smape_C{n_clients}.npy', smape_kd)
np.save(f'metrics/fedkd_mae_C{n_clients}.npy', mae_kd)
np.save(f'metrics/fedkd_rmse_C{n_clients}.npy', rmse_kd)

## 90

In [25]:
%%time
lstm_K5_kd = copy.deepcopy(lstm)
outputs_kd1, targets_kd1, loss_kd1, smape_kd1, mae_kd1, rmse_kd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_K5_kd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_kd, targets_kd, loss_kd, smape_kd, mae_kd, rmse_kd = fedkd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89]
round 0, starting client 1/90, id: 0
Epoch [1/1], Train Loss: 0.12927093012434135
round 0, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.11762646585702896
round 0, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.10258465094698797
round 0, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.10286813864813131
round 0, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.12376527759161864
round 0, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.11156913740560415
round 0, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.13374067138175705
round 0, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.11355552759091811
round 0, starting client 9/90, id: 8


C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.08007876845603842
round 1, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.06956384467581908
round 1, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.06009370665479864
round 1, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.06199816530387777
round 1, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.07461189741099425
round 1, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.06701788743957877
round 1, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.08297831821884658
round 1, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.06516808619336138
round 1, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.06774679291993378
round 1, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.05807290885907908
round 1, starting client 11/90, id: 10
Epoch [1/1], Train Loss: 0.08045284407368548
round 1, starting client 12/90, id: 11
Epoch [1/1], Train Loss: 0.05378385540097952
round 1, starting client 13/90, id: 12
Epoch [1/

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0508623074669883
round 2, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.041531991172167985
round 2, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.03751186586709485
round 2, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.04187417105205502
round 2, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.04486661362038416
round 2, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.041171259665861736
round 2, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.04872182394201693
round 2, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.03872578837118058
round 2, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.04485376569657371
round 2, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.03609021101146936
round 2, starting client 11/90, id: 10
Epoch [1/1], Train Loss: 0.05073216037514309
round 2, starting client 12/90, id: 11
Epoch [1/1], Train Loss: 0.03193922522232721
round 2, starting client 13/90, id: 12
Epoch [1

...

Epoch [1/1], Train Loss: 0.02766437825026376
round 4, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.022577523502210782
round 4, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.02513648631672064
round 4, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.025491048326241033
round 4, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.024811920519410214
round 4, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.023905015457421543
round 4, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.02627616597188486
round 4, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.02097826549467051
round 4, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.026698241350599203
round 4, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.019057631561601604
round 4, starting client 11/90, id: 10
Epoch [1/1], Train Loss: 0.02834576255797098
round 4, starting client 12/90, id: 11
Epoch [1/1], Train Loss: 0.01792311411056864
round 4, starting client 13/90, id: 12
Epo

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.01882347922315294
round 5, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.015479847674982415
round 5, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.018095775171079572
round 5, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.01917644403874874
round 5, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.0179181298325685
round 5, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.016981769737321885
round 5, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.017869215483802398
round 5, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.013973410742111362
round 5, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.020197697377835326
round 5, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.013977411069424336
round 5, starting client 11/90, id: 10
Epoch [1/1], Train Loss: 0.01951380122530585
round 5, starting client 12/90, id: 11
Epoch [1/1], Train Loss: 0.0127827644372653
round 5, starting client 13/90, id: 12
Epoc

C:\Users\User\Desktop\KD-FL\util.py:81: RuntimeWarning: invalid value encountered in double_scalars
  cluster_irregularities[label] = (cluster_irregularities[label] - min_irreg) / (max_irreg - min_irreg + 1e-8)


ValueError: Input contains NaN.

In [26]:
loss_kd = np.insert(loss_kd, 0, loss_kd1)
smape_kd = np.insert(smape_kd, 0, smape_kd1)
mae_kd = np.insert(mae_kd, 0, mae_kd1)
rmse_kd = np.insert(mae_kd, 0, mae_kd1)

In [27]:
np.save(f'metrics/fedkd_outputs_C{n_clients}.npy', np.array(outputs_kd, dtype=object))
np.save(f'metrics/fedkd_targets_C{n_clients}.npy', np.array(targets_kd, dtype=object))
np.save(f'metrics/fedkd_loss_C{n_clients}.npy', loss_kd)
np.save(f'metrics/fedkd_smape_C{n_clients}.npy', smape_kd)
np.save(f'metrics/fedkd_mae_C{n_clients}.npy', mae_kd)
np.save(f'metrics/fedkd_rmse_C{n_clients}.npy', rmse_kd)